Author：QYHcrossover
Date：2021-05-31

## 1.导入必要的库

In [1]:
import numpy as np
import pandas as pd
from collections import Counter
from sklearn import datasets

## 2.数据导入与预处理

### 2.1 导入肿瘤数据集

In [2]:
dataset = datasets.load_breast_cancer()
df = pd.DataFrame(data=np.hstack([dataset.data,dataset.target[:,np.newaxis]]),columns=[str(i) for i in dataset.feature_names]+["label"])
df

mean radius  mean texture  mean perimeter  mean area  mean smoothness  \
0         17.990         10.38          122.80     1001.0          0.11840   
1         20.570         17.77          132.90     1326.0          0.08474   
2         19.690         21.25          130.00     1203.0          0.10960   
3         11.420         20.38           77.58      386.1          0.14250   
4         20.290         14.34          135.10     1297.0          0.10030   
5         12.450         15.70           82.57      477.1          0.12780   
6         18.250         19.98          119.60     1040.0          0.09463   
7         13.710         20.83           90.20      577.9          0.11890   
8         13.000         21.82           87.50      519.8          0.12730   
9         12.460         24.04           83.97      475.9          0.11860   
10        16.020         23.24          102.70      797.8          0.08206   
11        15.780         17.89          103.60      781.0          0.09710   
12        19.170         24.80          132.40     1123.0          0.09740   
13        15.850         23.95          103.70      782.7          0.08401   
14        13.730         22.61           93.60      578.3          0.11310   
15        14.540         27.54           96.73      658.8          0.11390   
16        14.680         20.13           94.74      684.5          0.09867   
17        16.130         20.68          108.10      798.8          0.11700   
18        19.810         22.15          130.00     1260.0          0.09831   
19        13.540         14.36           87.46      566.3          0.09779   
20        13.080         15.71           85.63      520.0          0.10750   
21         9.504         12.44           60.34      273.9          0.10240   
22        15.340         14.26          102.50      704.4          0.10730   
23        21.160         23.04          137.20     1404.0          0.09428   
24        16.650         21.38          110.00      904.6          0.11210   
25        17.140         16.40          116.00      912.7          0.11860   
26        14.580         21.53           97.41      644.8          0.10540   
27        18.610         20.25          122.10     1094.0          0.09440   
28        15.300         25.27          102.40      732.4          0.10820   
29        17.570         15.05          115.00      955.1          0.09847   
..           ...           ...             ...        ...              ...   
539        7.691         25.44           48.34      170.4          0.08668   
540       11.540         14.44           74.65      402.9          0.09984   
541       14.470         24.99           95.81      656.4          0.08837   
542       14.740         25.42           94.70      668.6          0.08275   
543       13.210         28.06           84.88      538.4          0.08671   
544       13.870         20.70           89.77      584.8          0.09578   
545       13.620         23.23           87.19      573.2          0.09246   
546       10.320         16.35           65.31      324.9          0.09434   
547       10.260         16.58           65.85      320.8          0.08877   
548        9.683         19.34           61.05      285.7          0.08491   
549       10.820         24.21           68.89      361.6          0.08192   
550       10.860         21.48           68.51      360.5          0.07431   
551       11.130         22.44           71.49      378.4          0.09566   
552       12.770         29.43           81.35      507.9          0.08276   
553        9.333         21.94           59.01      264.0          0.09240   
554       12.880         28.92           82.50      514.3          0.08123   
555       10.290         27.61           65.67      321.4          0.09030   
556       10.160         19.59           64.73      311.7          0.10030   
557        9.423         27.88           59.26      271.3          0.08123   
558       14.590         22

### 2.2 数据标准化

In [3]:
X,y = dataset.data,dataset.target
X_std = (X-X.mean(axis=0)) / X.std(axis=0)
print(X_std)

[[ 1.09706398 -2.07333501  1.26993369 ...  2.29607613  2.75062224
   1.93701461]
 [ 1.82982061 -0.35363241  1.68595471 ...  1.0870843  -0.24388967
   0.28118999]
 [ 1.57988811  0.45618695  1.56650313 ...  1.95500035  1.152255
   0.20139121]
 ...
 [ 0.70228425  2.0455738   0.67267578 ...  0.41406869 -1.10454895
  -0.31840916]
 [ 1.83834103  2.33645719  1.98252415 ...  2.28998549  1.91908301
   2.21963528]
 [-1.80840125  1.22179204 -1.81438851 ... -1.74506282 -0.04813821
  -0.75120669]]


### 2.3 划分为训练集和测试集

In [5]:
import random
random_index = list(range(len(y)))
random.shuffle(random_index)
train_index = random_index[:-100]
test_index = random_index[-100:]
train_X,train_y = X[train_index,:],y[train_index]
print("X_train shape:",train_X.shape,"train_y shape:",train_y.shape)
test_X,test_y = X[test_index,:],y[test_index]
print("test_X shape:",test_X.shape,"test_y shape:",test_y.shape)

X_train shape: (469, 30) train_y shape: (469,)
test_X shape: (100, 30) test_y shape: (100,)


## 3.分类算法手动实现

### 3.1 KNN最近邻

#### 3.1.1 KNN算法实现

In [6]:
class KNNclassifier:
    def __init__(self,k):
        assert k>=1,"k必须是大于1的整数"
        self.k=k
        self.X_train=None
        self.y_train=None

    def fit(self,X_train,y_train):
        self.X_train=X_train
        self.y_train=y_train
        return self

    def _predict(self,X):
        distance = [np.sum((X_i-X)**2) for X_i in self.X_train]
        arg = np.argsort(distance)
        top_k = [self.y_train[i] for i in arg[:self.k]]
        # c=Counter(top_k)
        # return c.most_common(1)[0][0]
        counter={}
        for i in top_k:
            counter.setdefault(i,0)
            counter[i]+=1
        sort=sorted(counter.items(),key=lambda x:x[1])
        return sort[0][0]

    def predict(self, X_test):
        y_predict = [self._predict(i) for i in X_test]
        return np.array(y_predict)

    def accuracy(self, X_test ,y_test):
        y_predict = self.predict(X_test)
        return np.sum(y_predict==y_test)/len(X_test)

#### 3.1.2 KNN效果评估

In [7]:
for k in range(1,11):
    print("k",k)
    my_KNN=KNNclassifier(k)
    my_KNN.fit(train_X,train_y)
    y_predict=my_KNN.predict(test_X)
#     print("y_test:","\n",test_y)
#     print("y_predict","\n",y_predict)
    print("accuracy:",my_KNN.accuracy(test_X, test_y))

k 1
accuracy: 0.93
k 2
accuracy: 0.93
k 3
accuracy: 0.86
k 4
accuracy: 0.87
k 5
accuracy: 0.82
k 6
accuracy: 0.82
k 7
accuracy: 0.78
k 8
accuracy: 0.78
k 9
accuracy: 0.75
k 10
accuracy: 0.77


### 3.2 逻辑回归

#### 3.2.1 逻辑回归算法实现

In [8]:
class LogisticRegression:
    def __init__(self,lr=0.001,thr=1e-2,max_epoch=100000): #学习率和阈值
        self.lr = lr
        self.thr = thr
        self.max_epoch = max_epoch
        self.best_loss = np.inf
        self.best_theta = None

    def predict(self,X):
#         sigmoid = lambda x: 1/(1+np.exp(-x))
        #计算结果
        T = X@self.theta
        data = np.array(T,copy=True)
        pos_index = data>=0
        neg_index = data<0
        pos = 1.0/(1+np.exp(-data))
        data[pos_index] = pos[pos_index]
        neg = np.exp(data)/(1+np.exp(data))
        data[neg_index] = neg[neg_index]
#         print("data",data)
        return data

    def fit(self,X,y):
        #构造扩展的X
        paddedX = np.ones([X.shape[0],X.shape[1]+1])
        paddedX[:,:-1] = X
        #构造theta
        self.theta = np.random.randn(X.shape[-1]+1)[:,np.newaxis]
        #开始训练
        epoch = 0
        while True:
            #计算loss
            loss = 1/X.shape[0]*np.squeeze(-1*y.T@np.log(self.predict(paddedX)+1e-6) + -1*(1-y).T@np.log(1-self.predict(paddedX)+1e-6))
            if loss<self.best_loss:
                self.best_loss = loss
                self.best_theta = self.theta
            print("第{}epoch,loss为{}".format(epoch,loss))
            #计算梯度
            grad = paddedX.T@(self.predict(paddedX)-y)
#             print(grad)
            #是否收敛
            if abs(np.sum(grad)) < self.thr or epoch>self.max_epoch:
                break
            #梯度下降
            self.theta -= self.lr * grad
            epoch += 1
    
    def accuracy(self,test_X ,test_y):
        self.theta = self.best_theta
        paddedX = np.ones([test_X.shape[0],test_X.shape[1]+1])
        paddedX[:,:-1] = test_X
        predict_y = np.squeeze(self.predict(paddedX).astype(np.int))
        return np.sum(predict_y==test_y)/len(test_y)

#### 3.2.2 逻辑回归训练

In [9]:
lr = LogisticRegression(lr=0.01,max_epoch=100000)
lr.fit(train_X,train_y[:,np.newaxis])

第0epoch,loss为8.82084556814355
第1epoch,loss为5.155040626106386
第2epoch,loss为8.66046893185839
第3epoch,loss为5.155040626106386
第4epoch,loss为8.66046893185839
第5epoch,loss为5.125583245385781
第6epoch,loss为8.66046893185839
第7epoch,loss为8.66046893185839
第8epoch,loss为5.155040626106386
第9epoch,loss为8.66046893185839
第10epoch,loss为5.155040626106386
第11epoch,loss为8.66046893185839
第12epoch,loss为8.66046893185839
第13epoch,loss为5.155040626106386
第14epoch,loss为8.66046893185839
第15epoch,loss为5.155040626106386
第16epoch,loss为8.66046893185839
第17epoch,loss为1.7968992239574084
第18epoch,loss为8.66046893185839
第19epoch,loss为5.155040626106386
第20epoch,loss为8.66046893185839
第21epoch,loss为5.00775372250336
第22epoch,loss为8.66046893185839
第23epoch,loss为7.953491794563868
第24epoch,loss为5.155040626106386
第25epoch,loss为8.66046893185839
第26epoch,loss为5.155040626106386
第27epoch,loss为8.66046893185839
第28epoch,loss为1.2961237517071227
第29epoch,loss为7.776747510240238
第30epoch,loss为5.155040626106386
第31epoch,loss为8.66046893185839
第

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:16: RuntimeWarning: overflow encountered in exp
  app.launch_new_instance()


第101epoch,loss为8.542639408975969
第102epoch,loss为4.153489681605814
第103epoch,loss为8.60155417041718
第104epoch,loss为3.652714209355528
第105epoch,loss为8.395352505372944
第106epoch,loss为4.182947062326419
第107epoch,loss为8.542639408975969
第108epoch,loss为3.8000011129585527
第109epoch,loss为8.454267266814155
第110epoch,loss为4.0062027780027885
第111epoch,loss为8.513182028255365
第112epoch,loss为3.9472880165615787
第113epoch,loss为8.513182028255365
第114epoch,loss为3.829458493679158
第115epoch,loss为8.336437743931734
第116epoch,loss为3.9472880165615787
第117epoch,loss为8.336437743931734
第118epoch,loss为3.770543732237948
第119epoch,loss为8.012406556005079
第120epoch,loss为3.917830635840973
第121epoch,loss为8.248065601769918
第122epoch,loss为3.6821715900761327
第123epoch,loss为7.747290129519633
第124epoch,loss为3.9472880165615787
第125epoch,loss为8.041863936725683
第126epoch,loss为3.5348846864731076
第127epoch,loss为7.423258941592977
第128epoch,loss为3.8589158743997634
第129epoch,loss为7.953491794563868
第130epoch,loss为3.6232568286349225
第1

第358epoch,loss为1.2372089902659125
第359epoch,loss为2.032558269722249
第360epoch,loss为1.2077516095453074
第361epoch,loss为2.032558269722249
第362epoch,loss为1.2372089902659125
第363epoch,loss为2.032558269722249
第364epoch,loss为1.2077516095453074
第365epoch,loss为2.0031008890016437
第366epoch,loss为1.2077516095453074
第367epoch,loss为2.032558269722249
第368epoch,loss为1.2372089902659125
第369epoch,loss为2.150387792604669
第370epoch,loss为1.2961237517071227
第371epoch,loss为2.0031008890016437
第372epoch,loss为1.2077516095453074
第373epoch,loss为2.0031008890016437
第374epoch,loss为1.2077516095453074
第375epoch,loss为2.0031008890016437
第376epoch,loss为1.2077516095453074
第377epoch,loss为2.032558269722249
第378epoch,loss为1.2372089902659125
第379epoch,loss为2.062015650442755
第380epoch,loss为1.2372089902659125
第381epoch,loss为2.0031008890016437
第382epoch,loss为1.2372089902659125
第383epoch,loss为2.2093025540458786
第384epoch,loss为1.2961237517071225
第385epoch,loss为2.120930411884064
第386epoch,loss为1.2961237517071227
第387epoch,loss为2.09147

第655epoch,loss为1.3255811324277278
第656epoch,loss为1.0604647059422823
第657epoch,loss为1.3844958938689378
第658epoch,loss为1.0604647059422823
第659epoch,loss为1.3255811324277278
第660epoch,loss为1.0604647059422823
第661epoch,loss为1.3844958938689378
第662epoch,loss为1.0604647059422823
第663epoch,loss为1.2961237517071227
第664epoch,loss为1.0604647059422823
第665epoch,loss为1.3844958938689378
第666epoch,loss为1.0604647059422823
第667epoch,loss为1.3255811324277278
第668epoch,loss为1.0899220866628874
第669epoch,loss为1.3844958938689378
第670epoch,loss为1.0604647059422823
第671epoch,loss为1.3255811324277278
第672epoch,loss为1.0899220866628874
第673epoch,loss为1.3844958938689378
第674epoch,loss为1.0604647059422823
第675epoch,loss为1.3255811324277278
第676epoch,loss为1.0899220866628874
第677epoch,loss为1.3844958938689378
第678epoch,loss为1.0604647059422823
第679epoch,loss为1.3255811324277278
第680epoch,loss为1.0899220866628874
第681epoch,loss为1.3943322604086772
第682epoch,loss为1.0604647059422823
第683epoch,loss为1.3550385131483331
第684epoch,loss

...

第97728epoch,loss为1.2372089902659122
第97729epoch,loss为1.1488368481040974
第97730epoch,loss为1.3550385131483322
第97731epoch,loss为1.2077516095453074
第97732epoch,loss为1.4139532745895427
第97733epoch,loss为1.1782942288247025
第97734epoch,loss为1.4728680360307527
第97735epoch,loss为1.2077516095453076
第97736epoch,loss为1.4728680360307527
第97737epoch,loss为1.2077516095453076
第97738epoch,loss为1.4728680360307527
第97739epoch,loss为1.1782942288247025
第97740epoch,loss为1.4139532745895427
第97741epoch,loss为1.1782942288247025
第97742epoch,loss为1.4434106553101473
第97743epoch,loss为1.1782942288247025
第97744epoch,loss为1.4139532745895427
第97745epoch,loss为1.2077516095453074
第97746epoch,loss为1.3550385131483322
第97747epoch,loss为1.1488368481040974
第97748epoch,loss为1.266666370986517
第97749epoch,loss为1.1488368481040974
第97750epoch,loss为1.3255811324277273
第97751epoch,loss为1.1488368481040974
第97752epoch,loss为1.266666370986517
第97753epoch,loss为1.1193794673834923
第97754epoch,loss为1.266666370986517
第97755epoch,loss为1.119379467383

第98227epoch,loss为1.2666663709865178
第98228epoch,loss为1.6496123203543829
第98229epoch,loss为1.2961237517071227
第98230epoch,loss为1.6496123203543829
第98231epoch,loss为1.2666663709865178
第98232epoch,loss为1.5612401781925678
第98233epoch,loss为1.2666663709865178
第98234epoch,loss为1.6496123203543829
第98235epoch,loss为1.2961237517071227
第98236epoch,loss为1.6496123203543829
第98237epoch,loss为1.2666663709865178
第98238epoch,loss为1.5317827974719627
第98239epoch,loss为1.2372089902659127
第98240epoch,loss为1.6201549396337778
第98241epoch,loss为1.2666663709865178
第98242epoch,loss为1.5906975589131729
第98243epoch,loss为1.2666663709865178
第98244epoch,loss为1.5906975589131729
第98245epoch,loss为1.2666663709865178
第98246epoch,loss为1.6496123203543829
第98247epoch,loss为1.2666663709865178
第98248epoch,loss为1.5317827974719627
第98249epoch,loss为1.2372089902659127
第98250epoch,loss为1.5906975589131729
第98251epoch,loss为1.2666663709865178
第98252epoch,loss为1.6496123203543829
第98253epoch,loss为1.2666663709865178
第98254epoch,loss为1.502325416

第98727epoch,loss为1.1488368481040974
第98728epoch,loss为1.2961237517071222
第98729epoch,loss为1.1488368481040974
第98730epoch,loss为1.3255811324277273
第98731epoch,loss为1.1488368481040974
第98732epoch,loss为1.266666370986517
第98733epoch,loss为1.1488368481040974
第98734epoch,loss为1.3255811324277273
第98735epoch,loss为1.2077516095453074
第98736epoch,loss为1.3255811324277273
第98737epoch,loss为1.2077516095453074
第98738epoch,loss为1.3255811324277273
第98739epoch,loss为1.2077516095453074
第98740epoch,loss为1.3255811324277273
第98741epoch,loss为1.2077516095453074
第98742epoch,loss为1.2961237517071222
第98743epoch,loss为1.1488368481040974
第98744epoch,loss为1.2372089902659122
第98745epoch,loss为1.1193794673834923
第98746epoch,loss为1.2961237517071222
第98747epoch,loss为1.1488368481040974
第98748epoch,loss为1.3255811324277273
第98749epoch,loss为1.1488368481040974
第98750epoch,loss为1.266666370986517
第98751epoch,loss为1.1488368481040974
第98752epoch,loss为1.3255811324277273
第98753epoch,loss为1.1782942288247025
第98754epoch,loss为1.26666637098

第99226epoch,loss为1.0899220866628874
第99227epoch,loss为0.9426351830598618
第99228epoch,loss为1.0899220866628874
第99229epoch,loss为0.9426351830598618
第99230epoch,loss为1.0899220866628874
第99231epoch,loss为0.9426351830598618
第99232epoch,loss为1.0899220866628874
第99233epoch,loss为0.9426351830598618
第99234epoch,loss为1.0899220866628874
第99235epoch,loss为0.9426351830598618
第99236epoch,loss为1.0899220866628874
第99237epoch,loss为0.9426351830598618
第99238epoch,loss为1.0899220866628874
第99239epoch,loss为0.9426351830598618
第99240epoch,loss为1.0899220866628874
第99241epoch,loss为0.9426351830598618
第99242epoch,loss为1.0899220866628874
第99243epoch,loss为0.9426351830598618
第99244epoch,loss为1.0899220866628874
第99245epoch,loss为0.9426351830598618
第99246epoch,loss为1.0899220866628874
第99247epoch,loss为0.9426351830598618
第99248epoch,loss为1.0899220866628874
第99249epoch,loss为0.9426351830598618
第99250epoch,loss为1.0899220866628874
第99251epoch,loss为0.9426351830598618
第99252epoch,loss为1.0899220866628874
第99253epoch,loss为0.942635183

第99726epoch,loss为1.2372089902659122
第99727epoch,loss为1.1193794673834923
第99728epoch,loss为1.2961237517071222
第99729epoch,loss为1.1193794673834923
第99730epoch,loss为1.2372089902659122
第99731epoch,loss为1.0899220866628874
第99732epoch,loss为1.2077516095453076
第99733epoch,loss为1.0604647059422823
第99734epoch,loss为1.1488368481040974
第99735epoch,loss为1.0015499445010723
第99736epoch,loss为1.1488368481040974
第99737epoch,loss为1.0015499445010723
第99738epoch,loss为1.1782942288247025
第99739epoch,loss为1.0015499445010723
第99740epoch,loss为1.1782942288247025
第99741epoch,loss为1.0015499445010723
第99742epoch,loss为1.1782942288247025
第99743epoch,loss为1.0015499445010723
第99744epoch,loss为1.1488368481040974
第99745epoch,loss为0.972092563780467
第99746epoch,loss为1.1193794673834923
第99747epoch,loss为1.001549944501072
第99748epoch,loss为1.0899220866628874
第99749epoch,loss为0.942635183059862
第99750epoch,loss为1.0899220866628874
第99751epoch,loss为0.942635183059862
第99752epoch,loss为1.0899220866628874
第99753epoch,loss为0.9426351830598

In [10]:
lr.best_loss

0.7953482794568367

#### 3.2.3 逻辑回归效果评估

In [11]:
lr.accuracy(test_X,test_y)

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:16: RuntimeWarning: overflow encountered in exp
  app.launch_new_instance()


0.91